# 1. Introduction <a id='Introduction'></a>

<b>What is the Premier League?</b>

The Premier League (often referred to as the English Premier League or the EPL outside England) is the top level of the English football league system. In 2019, as Manchester City and Liverpool contested a thrilling title race, a cumulative global audience of 3.2 billion for all programming watched the action, <a href="https://www.premierleague.com/news/1280062">an increase of six per cent on the previous season.</a> This rise in viewership numbers, combined with an increasingly engaged fanbase, has translated into a greater interest in Premier League related games and interactive content.

<b>What is the Fantasy Premier League?</b>

Fantasy football is a game in which participants assemble an imaginary team of real life footballers and score points based on those players' actual statistical performance or their perceived contribution on the field of play. The way the game works is simple: you pick eleven players, and whenever these players perform well in the live matches, they get points. A goal for a striker, for example, is worth 3 points, and a clean sheet (no goals conceded) is worth 6 points.

The Fantasy Premier League (abbreviated to FPL), in particular, is the world's largest fantasy league with over 6 million players. With attractive prizes (top FPL players in each region earn a ticket to watch their favourite football team, while the overall first place wins a cash prize), the FPL fanbase are often more engaged and fanatical about football.

<b>Reddit and the Premier League</b>

Reddit is a social news aggregation, web content rating, and discussion website. Posts are organized by subject into user-created boards called "subreddits", which cover a variety of topics including news, science, movies, and of course, football.

/r/PremierLeague/ is one such subreddit, where fans of the English Premier League aggregate and discuss the game. The subreddit is 8 years old and has 108,0000 members as of 2019.

/r/FantasyPL/ is a subreddit dedicated to the fantasy version of the EPL. The subreddit is also 8 years old, and surprisingly has more members than /r/PremierLeague, at 177,000.

<b>Preamble:</b>

<u>This project will be addressed from the perspective from the marketing team of the Fantasy Premier League (FantasyPL) App.</u>

The goals of this project will be outlined in the following section.

# 2. Problem Statement <a id='Problem Statement'></a>

As managers of the FPL app, we want to evaluate: 
<li>What kind of people surf the FPL reddit, and what kind of people surf the EPL reddit? Are there overlaps (same username) who surf both reddits, and what's the extent of this overlap?
<li> Overall sentiment for EPL and FPL reddits, is one more positive than the other?
<li> What type of content are posted in the EPL and FPL reddits respectively? What features differentiates an EPL post from an FPL post?
<br>
<br>
To frame the problem from a data science perspective, this is both an inference problem and a prediction problem:
<li> First, we need to create a classification model with sufficient predictive power that differentiates between the two reddits. We will apply a few different models here to evaluate differences in features selected and predictive power. Intuitively, the higher the predictive power, the better the model is at distinguishing between the two subreddits, and therefore the features it selects are better indicators of difference.
<li> Second, we need to find what features are characteristic of each reddit.
<li> Third, are there differences in what teams each subreddit discuss? E.g., is Manchester United popular in EPL, but unpopular in FPL? Are there differences in the type of comments made in each subreddit?</li>
    
Using this information, we should gather information that supports a targeted marketing campaign - i.e. how to appeal to the broader spectrum of people who watch EPL but don't play FPL. <b>If I want to create a targeted marketing campaign on r/EPL, how should I go about doing it?</b>

# 3. Table of Contents <a id='Table of Contents'></a>

- <a href='#Introduction'>1. Introduction</a>
- <a href='#Problem_Statement'>2. Problem Statement</a>
- <a href='#Table of Contents'>3. Table of Contents</a>
- <a href='#Data Imports'>4. Library Imports</a>

- <a href='#Data Gathering'>5. Data Gathering</a>
    - <a href='#Sample25'>5.1 Sampling 25 Posts from Reddit</a>    
    - <a href='#DataProper'>5.2 Data Gathering Proper</a>
- <a href='#Data Dictionary'>6. Data Dictionary</a>           
- <a href='#Shape Missingness'>7. Evaluating Shape and Missingness</a>    
    - <a href='#Overview FPL'>7.1. Overview of FPL data</a>  
    - <a href='#Overview EPL'>7.2. Overview of EPL data</a>  
    - <a href='#Measuring Missingness'>7.3 Measuring Missingness</a>  
    - <a href='#Analysis Shape Missingness'>7.4 Analysis of Shape and Missingness</a>
- <a href='#Cleaning and Preprocessing'>8. Data Cleaning and Preprocessing</a>  
    - <a href='#Cleaning Functions'>8.1 Cleaning and Encoding Functions</a>    
    - <a href='#Filling Missing'>8.2 Filling Missing Values</a>    
        - <a href='#Extract OCR'>8.2.1 Filling using OCR from Images</a>    
        - <a href='#Extract Tweet'>8.2.2 Filling using Tweet data</a>    
    - <a href='#Cleaning Text'>8.3. Cleaning, Tokenizing, and Lemmatizing Text</a>    
- <a href='#Sentiment Analysis'>8.4 Sentiment Analysis</a>  
    - <a href='#Cleaning Functions'>8.1 Cleaning and Encoding Functions</a>    

# 4. Library Imports <a id='Data Imports'></a>

In [1]:
#General Imports
import requests
import pandas as pd
import numpy as np
import time
import random
import math
from collections import namedtuple, Counter
import scipy.stats as stats
from scipy.stats import norm
import datetime

#Scraping Imports
import requests
from bs4 import BeautifulSoup

#NLP Imports
import spacy
import re
from textblob import TextBlob, Word, Blobber
from textblob.classifiers import NaiveBayesClassifier
from textblob.taggers import NLTKTagger
import nltk
from nltk.stem import WordNetLemmatizer 
from nltk import pos_tag, word_tokenize
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer


#Plotting/Graphs
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline

#OCR imports
from PIL import Image
import pytesseract
from io import BytesIO
#This line won't work unless you install tesseract OCR software
#Change the path to where you saved the program if you have it
pytesseract.pytesseract.tesseract_cmd = r'C:\Program Files\Tesseract-OCR\tesseract.exe'

#Modelling Imports
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import confusion_matrix, roc_auc_score
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.preprocessing import StandardScaler
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.linear_model import LogisticRegression
#Lets you view all columns in a dataframe when there are a LARGE number of columns
pd.set_option('display.max_columns', None)
#Fix for pandas truncating long strings (e.g. urls)
#If you don't run this, pandas will cut short your long urls and this breaks code that require urls
pd.set_option("display.max_colwidth", 10000)

# 5. Data Gathering <a id='Data Gathering'></a>

### 5.1 Sampling 25 posts from Reddit <a id='Sample25'></a> 
<div align="right"><a href='#Table of Contents'>Back to Table of Contents</a></div>

Before any serious crawling begins, there is a need to evaluate what the raw data looks like, what fields are necessary, what can be dropped, and any potential gaps in the data.

In [2]:
#Get the first 25 posts from the PremierLeague subreddit
url = 'https://www.reddit.com/r/PremierLeague/.json'
res = requests.get(url, headers={'User-agent': 'Ponyman1'})                
post_dict = res.json()
posts = [p['data'] for p in post_dict['data']['children']]
EPL_sample = pd.DataFrame(posts)
EPL_sample.head(3)

all_awardings  allow_live_comments approved_at_utc approved_by  archived  \
0            []                 True            None        None     False   
1            []                 True            None        None     False   
2            []                False            None        None     False   

           author author_flair_background_color author_flair_css_class  \
0       pumkinhat                          None                   None   
1  Sofishticated_                          None                    ava   
2         gibba97                          None                   None   

                                                                                                                 author_flair_richtext  \
0                                                                                                                                   []   
1  [{'a': ':ava:', 'e': 'emoji', 'u': 'https://emoji.redditmedia.com/hndntrmkiq131_t5_2scup/ava'}, {'e': 'text', 't': ' Aston Villa'}]   
2                                                                                                                                   []   

               author_flair_template_id  author_flair_text  \
0                                  None               None   
1  12a59dbc-8460-11e9-ba38-0ef0b9539158  :ava: Aston Villa   
2                                  None               None   

  author_flair_text_color author_flair_type author_fullname  \
0                    None              text        t2_rk9wt   
1                    dark          richtext       t2_13ejpc   
2                    None              text        t2_wzajn   

   author_patreon_flair awarders banned_at_utc banned_by  can_gild  \
0                 False       []          None      None     False   
1                 False       []          None      None     False   
2                 False       []          None      None     False   

   can_mod_post category  clicked content_categories  contest_mode  \
0         False     None    False               None         False   
1         False     None    False               None         False   
2         False     None    False               None         False   

        created   created_utc discussion_type distinguished  \
0  1.566045e+09  1.566016e+09            None          None   
1  1.566399e+09  1.566370e+09            None     moderator   
2  1.571686e+09  1.571658e+09            None          None   

               domain  downs  edited  gilded gildings  hidden  hide_score  \
0  self.PremierLeague      0   False       0       {}   False       False   
1  self.PremierLeague      0   False       0       {}   False       False   
2  self.PremierLeague      0   False       0       {}   False       False   

       id  is_crosspostable  is_meta  is_original_content  \
0  crhhzv             False    False                False   
1  ctd3bt             False    False                False   
2  dkz6tb             False    False                False   

   is_reddit_media_domain  is_robot_indexable  is_self  is_video likes  \
0                   False                True     True     False  None   
1                   False                True     True     False  None   
2                   False                True     True     False  None   

  link_flair_background_color link_flair_css_class  \
0                     #7193ff                        
1                     #7193ff                        
2                     #7193ff                        

                      link_flair_richtext  \
0      [{'e': 'text', 't': 'Discussion'}]   
1  [{'e': 'text', 't': 'Moderator Post'}]   
2        [{'e': 'text', 't': 'Question'}]   

                 link_flair_template_id link_flair_text link_flair_text_color  \
0  9f833a4a-8ee9-11e8-9ddc-0e618b2b6a52      Discussion                 light   
1  19119140-8da4-11e9-8b74-0e0bd0a9a746  Moderator Post                 light   
2  86fb4972-8ee9-11e8-ab9f-0ef

In [3]:
#Get the first 25 posts from the FantasyPL subreddit
url = 'https://www.reddit.com/r/fantasyPL/.json'
res = requests.get(url, headers={'User-agent': 'Ponyman1'})                
post_dict = res.json()
posts = [p['data'] for p in post_dict['data']['children']]
FPL_sample = pd.DataFrame(posts)
FPL_sample

all_awardings  allow_live_comments approved_at_utc approved_by  archived  \
0             []                 True            None        None     False   
1             []                 True            None        None     False   
2             []                 True            None        None     False   
3             []                False            None        None     False   
4             []                 True            None        None     False   
5             []                False            None        None     False   
6             []                 True            None        None     False   
7             []                False            None        None     False   
8             []                 True            None        None     False   
9             []                 True            None        None     False   
10            []                False            None        None     False   
11            []                False            None        None     False   
12            []                False            None        None     False   
13            []                 True            None        None     False   
14            []                False            None        None     False   
15            []                False            None        None     False   
16            []                 True            None        None     False   
17            []                False            None        None     False   
18            []                False            None        None     False   
19            []                 True            None        None     False   
20            []                False            None        None     False   
21            []                False            None        None     False   
22            []                 True            None        None     False   
23            []                 True            None        None     False   
24            []                False            None        None     False   
25            []                False            None        None     False   
26            []                 True            None        None     False   

               author author_flair_background_color author_flair_css_class  \
0        FPLModerator                                                        
1        FPLModerator                                                        
2          Ak_Ibrahim                                                 None   
3           JLane1996                                               points   
4           FPLFeeker                                                 None   
5                3amz                                                 None   
6            Sad_Weed                                                        
7   strawberrygenius7                                                        
8        QuickyGaming                                                 None   
9       cguinnesstout                                               points   
10            kayeloo                                                 None   
11      fromdowntownn                                                        
12             FMLFPL                                                 None   
13      superstoreman                          None              tottenham   
14      cguinnesstout                                               points   
15              mrdiv                                                 None   
16          chapalang                          None                   None   
17          FPLFeeker                                                 None   
18          FPLFeeker                                                 None   
19   aurorabortrealis                                                        
20       Mik-Hail-tal                                                 None   
21           DoTheRax                          None                   None

In [4]:
#Check if the columns tally - are there any features that are in the EPL subreddit but not in the FPL subreddit?
print('FPL columns: {} \nEPL columns: {}'.format(len(FPL_sample.columns), len(EPL_sample.columns)))

FPL columns: 103 
EPL columns: 103


In [5]:
#Find difference in features; are the differences important?
[n for n in EPL_sample.columns if n not in FPL_sample.columns]

[]

<b>Issues Observed</b>

There are a few issues with the data as it currently is:

<li>Redundant columns - there are over 100! Only the following fields will be kept: 'subreddit_name_prefixed', 'author', 'title', 'selftext', 'domain', 'link_flair_text', 'created', 'media', 'media_embed', 'url', 'permalink', 'num_comments', 'score', 'ups'. These are the fields with data relevant to our analysis, and will be further elaborated on in the data dictionary.</li>
<br>

<li> Missing comments; will have to create a separate process to extract comments from each post </li>
<br>

<li> Some posts don't have text (null values) as they're links to websites or image posts. There are two ways to resolves this:
    for links, there are excerpts we can use in place of selftext, and for images, we can use OCR.</li>
 <br>   
    
<li> Column numbers don't tally for the two subreddits, but the two/three additional columns are not relevant to our analysis so we will drop this (crosspost_parent, crosspost_parent_list, media_metadata). The additional columns (e.g. media_metadata) depend on the content posted in linkposts.

### 5.2 Data Gathering Proper  <a id='DataProper'></a> 
<div align="right"><a href='#Table of Contents'>Back to Table of Contents</a></div>

<font color="red"><b>LONG RUNTIME WARNING - the code below takes 15 - 30 minutes to run depending on loop settings!
    
Set comment_count to 1 to pull only 1 comment if testing code, as this cuts down on run time.</b></font>

In [ ]:
#This code takes quite some time to run - between 15-30 minutes depending on the scope.
#Args: total_loops - number of pages to crawl (if each page has 100, run total_loops = 10)
#      comment_count - number of comments per post to extract
#      filename - suffix to use when saving intermediate files to local drive
    
def crawl_reddit(link, total_loops=1, comment_count=5, filename = 'subreddit'):
    
    #Set of fake names to use under 'user-agent' to access reddit
    fake_name = ['Horse', 'Pony', 'Chihuahua', 'Donkey', 'Rabbit', 'Chicken', 'Duck']
    
    #Fields to keep in the output dataframe
    fields = ['subreddit_name_prefixed', 'author', 'title', 'selftext', 'domain', 'link_flair_text', 'created', 
              'media', 'media_embed', 'url', 'permalink', 'num_comments', 'score', 'ups']
    next_link = ""
    
    for i in range(total_loops):
        #Code for first loop is different, because it initiates a new dataframe and creates new variables.
        if i == 0:
            print('Starting crawl of page {}'.format(i+1))
            url = link
            res = requests.get(url, headers={'User-agent': 
                                             fake_name[np.random.randint(6)]+str(np.random.randint(10))})
            post_dict = res.json()
            next_link = post_dict['data']['after']   #retrieves 'after' key from json needed to get next n posts
            posts = [p['data'] for p in post_dict['data']['children']]
            df = pd.DataFrame(posts)[fields]
            df['comments'] = '' #initialize an empty series to put values into
           
            #Extracts top n comments from each post
            for count, post in enumerate(df['permalink']):
                res = requests.get('https://reddit.com'+post+'.json', headers={'User-agent': 
                                                                               fake_name[np.random.randint(6)]+str(np.random.randint(10))})
                comment_dict = res.json()
                comments = []

                #if number of comments is less than comment_count, return number of comments, otherwise return comment_count

                for comment in range(0, len(comment_dict[1]['data']['children'])-1 if len(comment_dict[1]['data']['children'])-1 < comment_count-1 else comment_count-1):
                    comments += [comment_dict[1]['data']['children'][comment]['data']['body']]
                    df.at[count, 'comments'] = comments
                                  
        else:
            #Breaks loop if there is no 'after' key in the json (i.e. no more posts)
            if next_link is None:
                print('Crawl terminated after {} loops: no more posts!'.format(i+1))
                return df
                break
            
            #Runs if it's not the first page. Creates a new placeholder dataframe to append to the first post dataframe
            else:
                print('Starting crawl of page {}'.format(i+1))
                url = link + '&after=' + next_link
                res = requests.get(url, headers={'User-agent': fake_name[np.random.randint(6)]+str(np.random.randint(10))})
                post_dict = res.json()
                next_link = post_dict['data']['after']
                posts = [p['data'] for p in post_dict['data']['children']]
                df_new = pd.DataFrame(posts)[fields]
                
                #Extract top n comments from each post
                for count, post in enumerate(df_new['permalink']):
                    res = requests.get('https://reddit.com'+post+'.json', headers={'User-agent': fake_name[np.random.randint(6)]+str(np.random.randint(10))})
                    comment_dict = res.json()
                    comments = []

                    #if number of comments is less than comment_count, return number of comments, otherwise return comment_count

                    for comment in range(0, len(comment_dict[1]['data']['children'])-1 if len(comment_dict[1]['data']['children'])-1 < comment_count-1 else comment_count-1):
                        comments += [comment_dict[1]['data']['children'][comment]['data']['body']]
                        df_new.at[count, 'comments'] = comments          

                df = df.append(df_new, ignore_index = True)
        
        #Saves a temporary file in the raw_data folder in case the function terminates or your computer explodes
        df.to_csv(r".\raw_data\reddit_"+ filename + str(i+1)+".csv")
        print('file saved!')
        
    return df

In [7]:
df_fpl = crawl_reddit('https://www.reddit.com/r/FantasyPL/new.json?limit=100', total_loops = 10, 
                      comment_count = 10, filename = 'FPL')

Starting crawl of page 1
file saved!
Starting crawl of page 2
file saved!
Starting crawl of page 3
file saved!
Starting crawl of page 4
file saved!
Starting crawl of page 5
file saved!
Starting crawl of page 6
file saved!
Starting crawl of page 7
file saved!
Starting crawl of page 8
file saved!
Starting crawl of page 9
file saved!
Starting crawl of page 10
file saved!


In [8]:
df_epl = crawl_reddit('https://www.reddit.com/r/PremierLeague/new.json?limit=100', total_loops = 10, 
                      comment_count = 10, filename = 'EPL')

Starting crawl of page 1
file saved!
Starting crawl of page 2
file saved!
Starting crawl of page 3
file saved!
Starting crawl of page 4
file saved!
Starting crawl of page 5
file saved!
Starting crawl of page 6
file saved!
Starting crawl of page 7
file saved!
Starting crawl of page 8
file saved!
Starting crawl of page 9
file saved!
Starting crawl of page 10
file saved!


In [9]:
#Save files to local drive for cleaning/EDA:
df_fpl.to_csv(r".\datasets\reddit_FPL_1_v2.csv")
df_epl.to_csv(r".\datasets\reddit_EPL_1_v2.csv")

# 6. Data Dictionary  <a id='Data Dictionary'></a> 
<div align="right"><a href='#Table of Contents'>Back to Table of Contents</a></div>

There are over 100 columns in the data dump the Reddit API provides.
The dictionary below covers the relevant fields extracted from the API, and the engineered fields which will be covered in later sections.

|Feature|Type|Description|Analysis|
|---|---|---|---|
|subreddit_name_prefixed|string/object|Name of the subreddit| Used as target for classification|
|author|string/object|User name of who made the main post| |
|title|string/object|Title of the post| To be included in bag of words|
|selftext|string/object|A self post is a text post, instead of a link post. A link post directs to an external link. A self post is nothing but the text you enter.| To be included in bag of words|
|domain|string/object|For link posts, domain captures the website the link belongs to. For self posts, the domain captures the subreddit the post was made in. |Used to differentiate between link post and self post. Self posts have a domain beginning with 'self'|
|link_flair_text|string/object|What category the post falls under - differs from subreddit to subreddit|Can run a barplot to get a sense of categories in the subreddit|
|created|float|When the post was made|Will be mapped to return date only; remove time data|
|media|string/object|For link posts, the type of link attached (e.g. Twitter, Facebook, news site)|Can extract tweet content from this field using a regex|
|media_embed|string/object|Description of link post| |
|url|string/object|External link, for link posts|Run through OCR if image|
|permalink|string/object|Permanent link to post|Used to loop through post for comments in crawler|
|num_comments|int64|Number of comments made on the post||
|score|int64|Number of upvotes - number of downvotes||
|ups|int64|Number of upvotes| |
|comments|string/object|List of up to 10 comments extracted from the comments made in the post| Engineered field - To be included in bag of words|

# 7. Evaluating Shape and Missingness  <a id='Shape Missingness'></a> 
<div align="right"><a href='#Table of Contents'>Back to Table of Contents</a></div>

In [60]:
df_fpl = pd.read_csv(r".\datasets\reddit_FPL_1.csv")

In [61]:
df_epl = pd.read_csv(r".\datasets\reddit_EPL_1.csv")

###   7.1 Quick overview of FPL dataframe  <a id='Overview FPL'></a> 
<div align="right"><a href='#Table of Contents'>Back to Table of Contents</a></div>

In [62]:
df_fpl.head(3)

Unnamed: 0 subreddit_name_prefixed        author  \
0           0             r/FantasyPL      DoTheRax   
1           1             r/FantasyPL  QuickyGaming   
2           2             r/FantasyPL      Sad_Weed   

                                                                                    title  \
0                                     Average of GW 9 is higher than the average of GW 8.   
1  Lundstram would have scored points 34 if he was correctly categorized as a midfielder.   
2                                          Also consider Lundstram as a potential starter   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     selftext  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       Can someone please explain to me how this gw's average is higher than the previous gw? Despite highly owned players like Mane and Abraham exploding. Also despite returns from Burnley defenders, Mount, Lundstram, a cheeky TAA bonus in the previous gameweek, we have a higher gw average this week with literally no one who is significantly owned returning/exploding except a 5, 6, and 8 from Sterling, Lundstram and Robbo. I really don't understand the maths behind this.   
1  These calculations will be really long, there's no real purpose in it other than to be a filler so this post doesn't get removed. Also the bonus points might have been different but I'm not sure how to calculate them.\n\nNote: Lundstram is currently on 45 points in his current, miscategorized state.\n\nGW 1: BOU (A) - 2 points for playing 77 minutes, 1 bonus point = 3 points\n\nGW 2: CRY (H) - 2 points for playing 90 minutes, 5 points for 1 goal scored, 1 point for a clean sheet, -1 point for a yellow card, 3 bonus points = 10 points\n\nGW 3: LEI (H) - 2 points for playing 90 minutes, -1 point for a yellow card = 1 point\n\nGW 4: CHE (A) - 2 po

In [63]:
df_fpl.shape

(990, 16)

In [64]:
df_fpl.dtypes

Unnamed: 0                   int64
subreddit_name_prefixed     object
author                      object
title                       object
selftext                    object
domain                      object
link_flair_text             object
created                    float64
media                       object
media_embed                 object
url                         object
permalink                   object
num_comments                 int64
score                        int64
ups                          int64
comments                    object
dtype: object

### 7.2 Quick overview of EPL dataframe  <a id='Overview ePL'></a> 
<div align="right"><a href='#Table of Contents'>Back to Table of Contents</a></div>

In [65]:
df_epl.head(3)

Unnamed: 0 subreddit_name_prefixed               author  \
0           0         r/PremierLeague  AngelrentiriaChivas   
1           1         r/PremierLeague           misomiso82   
2           2         r/PremierLeague            Wuz314159   

                                                                                                                        title  \
0                                                                                   Lil peep wearing premier league clothing!   
1  NOOB question - why are Leicester city doing so well this season so far - is it the fixture list or are they playing well?   
2                                                          What if, and hear me out.... Arsène wasn't the problem at Arsenal?   

                                                                                                                                                                                                                                         selftext  \
0                                                                                                                                                                                                                                             NaN   
1  Have only been following a little yet am just a little surprised to see them so high.  Just wandering if it's been a good fixture list or if they have a new player, or are doing something tactically etc.\n\n&amp;#x200B;\n\nTy for any info   
2                                                                                                                                                                                                                                             NaN   

               domain link_flair_text       created media media_embed  \
0           i.redd.it      Discussion  1.571734e+09   NaN          {}   
1  self.PremierLeague        Question  1.571723e+09   NaN          {}   
2  self.PremierLeague      Discussion  1.571720e+09   NaN          {}   

                                                                                                        url  \
0                                                                       https://i.redd.it/c9wtp9h7pzt31.jpg   
1     https://www.reddit.com/r/PremierLeague/comments/dl7kbt/noob_question_why_are_leicester_city_doing_so/   
2  https://www.reddit.com/r/PremierLeague/comments/dl6vjb/what_if_and_hear_me_out_arsène_wasnt_the_problem/   

                                                                            permalink  \
0          /r/PremierLeague/comments/dl9z8s/lil_peep_wearing_premier_league_clothing/   
1     /r/PremierLeague/comments/dl7kbt/noob_question_why_are_leicester_city_doing_so/   
2  /r/PremierLeague/comments/dl6vjb/what_if_and_hear_me_out_arsène_wasnt_the_problem/   

   num_comments  score  ups  \
0             2      0    0   
1             8      1    1   
2             5     39   39   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

In [66]:
df_epl.shape

(997, 16)

In [67]:
df_epl.dtypes

Unnamed: 0                   int64
subreddit_name_prefixed     object
author                      object
title                       object
selftext                    object
domain                      object
link_flair_text             object
created                    float64
media                       object
media_embed                 object
url                         object
permalink                   object
num_comments                 int64
score                        int64
ups                          int64
comments                    object
dtype: object

#### 7.2.1 Filling empty cells with NaN 

> Some of the fields are empty, but not filled with NaN. I will replace any cells which = ' ' with np.nan to properly evaluate missingness. Importantly, the empty selftext fields do not show up as NaN, so running isnull() would give the wrong impression that all of EPL's posts are self text posts!

In [68]:
df_epl = df_epl.applymap(lambda x: np.nan if x == '' else x)
df_fpl = df_fpl.applymap(lambda x: np.nan if x == '' else x)

### 7.3 Measuring 'missingness'  <a id='Measuring Missingness'></a> 
<div align="right"><a href='#Table of Contents'>Back to Table of Contents</a></div>

In [69]:
pd.DataFrame(df_fpl.isnull().sum(), columns = ['FPL']).transpose()

Unnamed: 0  subreddit_name_prefixed  author  title  selftext  domain  \
FPL           0                        0       0      0       537       0   

     link_flair_text  created  media  media_embed  url  permalink  \
FPL              420        0    801            0    0          0   

     num_comments  score  ups  comments  
FPL             0      0    0        75

In [70]:
print(f'There are {df_fpl.isnull().sum().sum()} missing values!')

There are 1833 missing values!


In [71]:
pd.DataFrame(df_epl.isnull().sum(), columns = ['EPL']).transpose()

Unnamed: 0  subreddit_name_prefixed  author  title  selftext  domain  \
EPL           0                        0       0      0       489       0   

     link_flair_text  created  media  media_embed  url  permalink  \
EPL              285        0    958            0    0          0   

     num_comments  score  ups  comments  
EPL             0      0    0       295

In [72]:
print(f'There are {df_epl.isnull().sum().sum()} missing values!')

There are 2027 missing values!


### 7.4 Analysis of Shape and  Missingness  <a id='Analysis Shape Missingness'></a> 
<div align="right"><a href='#Table of Contents'>Back to Table of Contents</a></div>

<b>Overall Shape</b>

The number of posts from each subreddit extracted are close - 992 for FPL, and 996 for EPL.
This is a sufficient sample size for my analysis.

<b>Missingness</b>

For the majority of the columns, the missing values do not matter and can be filled with 0.
This applies to link_flair_text (implies the post doesn't have a flair), media (implies there's no media attachment), and comments (implies there are no comments for the post).

<b>Self posts vs Link posts</b>

The concern here is the selftext field - almost half the posts aren't self posts! These are link posts - which are basically a link to a website or an image. We could pull only self text posts for our analysis, but that could skew or bias our data.

Instead, we will fill these missing values with excerpts from the link, either through OCR or the link description in the following section.

# 8. Data Cleaning and Preprocessing  <a id='Cleaning and Preprocessing'></a> 
<div align="right"><a href='#Table of Contents'>Back to Table of Contents</a></div>

### 8.1 Data Cleaning and Encoding Functions  <a id='Cleaning Functions'></a>

In [73]:
#Removes duplicates and prints out number of duplicates removed
def remove_duplicates(my_df):
    before_d = len(my_df)
    my_df.drop_duplicates(inplace=True)
    after_d = len(my_df)
    print(str(before_d-after_d) + " duplicates were removed!")

In [74]:
#Converts image to text string
def ocr_core(filename):
    #Try/except handles 404 and other similar errors
    try:
        response = requests.get(filename)
        img = Image.open(BytesIO(response.content))
        text = pytesseract.image_to_string(img) 
        return text
    except:
        return np.nan

In [106]:
#Dictionary below captures html tags and formatting that I want to remove
#Creates a pattern to apply in regex
rep = {'"ltr"': "", '&gt': "", '&lt' : "", '&amp;#39' : "", 'br&gt' : " ", "p&gt" : "", ";quot" : "",
      "&amp" : "", "amp;": "", "mdash" : "",  ';' : ""}
rep = dict((re.escape(k), v) for k, v in rep.items()) 
pattern = re.compile("|".join(rep.keys())) #Creates pattern based on rep dictionary

#Extracts tweet content from media column in dataframe (which is in a bastardized html format)
def extract_tweet(tweet):
    #Try/except in case of formatting problems in the raw data.
    try:
        twit_string = pattern.sub(lambda x: rep[re.escape(x.group(0))], tweet) #gets rid of html tags
        twit_string = re.search('dir=(.*)blockquote', twit_string) #finds main content of tweet based on html class
        twit_string = re.sub(r'(?s)(a href)(.*?)(\/a)', " ", twit_string.group(1)) #gets rid of embedded links
        return(twit_string)
    
    except:
        return np.nan

### 8.2 Filling Missing Values <a id='Filling Missing'></a> 
<div align="right"><a href='#Table of Contents'>Back to Table of Contents</a></div>

In [75]:
remove_duplicates(df_fpl)

0 duplicates were removed!


In [76]:
remove_duplicates(df_epl)

0 duplicates were removed!


Changing datetime data in 'created' column to date only:

In [77]:
df_fpl['created'] = df_fpl['created'].apply(lambda x: datetime.datetime.utcfromtimestamp(x).date())

In [78]:
df_epl['created'] = df_epl['created'].apply(lambda x: datetime.datetime.utcfromtimestamp(x).date())

#### 8.2.1 Extracting image content using OCR for link posts <a id='Extract OCR'></a> 

<font color="red"><b>LONG RUNTIME WARNING - the code below takes up to 15 minutes to run depending on the number of images!
Pytesseract requires additional installations outside of a pip install. Guide to installation <a href='https://stackoverflow.com/questions/50951955/pytesseract-tesseractnotfound-error-tesseract-is-not-installed-or-its-not-i'>HERE</a></b></font>

In [79]:
#Convert all picture (png and jpg) attachments to text; return results to new column in dataframe
df_epl['ocr'] = [ocr_core(picture) if ('.png' in picture or '.jpg' in picture) else np.nan for picture in df_epl['url']]
df_fpl['ocr'] = [ocr_core(picture) if ('.png' in picture or '.jpg' in picture) else np.nan for picture in df_fpl['url']]

In [80]:
#Checking OCR output
df_epl[df_epl['ocr'].notnull()][['url', 'ocr']]

url  \
0    https://i.redd.it/c9wtp9h7pzt31.jpg   
20   https://i.redd.it/uzrw1m09hjt31.jpg   
21   https://i.redd.it/uqqe58fh0jt31.png   
22   https://i.redd.it/m9tec2vfbit31.jpg   
27   https://i.redd.it/yzw4ttg0xbt31.png   
32   https://i.redd.it/wz0xhhy6l8t31.jpg   
42   https://i.redd.it/qpg89gcg0ss31.jpg   
46   https://i.redd.it/oxkxbsgeols31.jpg   
62   https://i.redd.it/ujadxjxsnsr31.jpg   
77   https://i.redd.it/417kh3fjqar31.jpg   
78   https://i.redd.it/blxj38pka8r31.jpg   
84   https://i.redd.it/zgj5z35nw1r31.png   
86   https://i.redd.it/3dxw1woanzq31.jpg   
89   https://i.redd.it/sqwb3936tyq31.jpg   
95   https://i.redd.it/0n89emtg3wq31.png   
100  https://i.redd.it/g6sy342yoqq31.jpg   
134  https://i.redd.it/awbwnymv7zo31.png   
170  https://i.redd.it/4v57v2f9nqn31.png   
180  https://i.redd.it/9eie7yze4ln31.png   
208  https://i.redd.it/2w4fx57padm31.jpg   
294  https://i.redd.it/03qv03op3oi31.png   
444  https://i.redd.it/nt1zw1pu2rf31.jpg   
470  https://i.redd.it/q4k3fav10ff31.jpg   
611  https://i.redd.it/bym7a4fyl3d31.png   
749  https://i.redd.it/em2mcdn53i931.jpg   
885  https://i.redd.it/bo9ycgr8o9331.jpg   
991  https://i.redd.it/rlkggvawisy21.jpg   
994  https://i.redd.it/205na54ixdy21.png   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 ocr  
0                                

In [81]:
#Number of entries created:
df_epl['ocr'].notnull().sum()

28

In [82]:
#Checking OCR output
df_fpl[df_fpl['ocr'].notnull()][['url', 'ocr']]

url  \
2    https://i.redd.it/v3pv564jezt31.jpg   
5    https://i.redd.it/y1sx8mgd0zt31.jpg   
8    https://i.redd.it/jksvmiwukyt31.jpg   
10   https://i.redd.it/c9voahepoxt31.jpg   
11   https://i.redd.it/52vhqweioxt31.png   
14   https://i.redd.it/qh6v6a82fwt31.jpg   
27   https://i.redd.it/af6e0gfv3rt31.jpg   
30   https://i.redd.it/2au0zjdkuqt31.jpg   
34   https://i.redd.it/iedhbmboipt31.png   
35   https://i.redd.it/ekz39lw6ipt31.jpg   
36   https://i.redd.it/jr5gp4yehpt31.jpg   
50   https://i.redd.it/e76i479anmt31.jpg   
67   https://i.redd.it/lq4h0o9foit31.jpg   
69   https://i.redd.it/qpim0dh67it31.jpg   
71   https://i.redd.it/86npphz42it31.jpg   
72   https://i.redd.it/beh56ygq0it31.jpg   
73   https://i.redd.it/qoihvhdpzht31.jpg   
75   https://i.redd.it/myvm24deyht31.jpg   
77   https://i.redd.it/yhfhe39xxht31.jpg   
78   https://i.redd.it/2mzkuqxsxht31.png   
79   https://i.redd.it/h7dnq7mnxht31.png   
80   https://i.redd.it/5fq5o5rixht31.jpg   
81   https://i.redd.it/w4g8vmshxht31.jpg   
82   https://i.redd.it/g0ep516juht31.png   
86   https://i.redd.it/w1scusn75ht31.png   
87   https://i.redd.it/kbuqx1mi6ht31.jpg   
89   https://i.redd.it/n95vacae6ht31.png   
102  https://i.redd.it/4tt4bu59bdt31.png   
106  https://i.redd.it/uibf474vgct31.png   
107  https://i.redd.it/hdacx45wfct31.jpg   
..                                   ...   
850  https://i.redd.it/wmvqnnb47so31.png   
851  https://i.redd.it/26qe8p1q6so31.png   
852  https://i.redd.it/1vk0x0by4so31.png   
853  https://i.redd.it/yhcdhuhk4so31.jpg   
854  https://i.redd.it/50dbvygb4so31.jpg   
855  https://i.redd.it/ikgospuz3so31.jpg   
856  https://i.redd.it/rl198g463so31.jpg   
857      https://i.imgur.com/giBZhWo.jpg   
858  https://i.redd.it/ai5xu103zro31.jpg   
870  https://i.redd.it/u7rwxm9pnpo31.png   
892  https://i.redd.it/xrrr1m5g7lo31.jpg   
893  https://i.redd.it/0zfl25fq1lo31.jpg   
894  https://i.redd.it/tvlxea1b1lo31.jpg   
896      https://i.imgur.com/lvWBixn.png   
897  https://i.redd.it/2me4oqqnyko31.jpg   
898  https://i.redd.it/pyefc268yko31.jpg   
899  https://i.redd.it/sl9rl49xxko31.jpg   
900  https://i.redd.it/lbgul9xkxko31.jpg   
902  https://i.redd.it/l1uk6km3oko31.png   
929  https://i.redd.it/0uc0td80neo31.jpg   
947  https://i.redd.it/gtjv9bwy0co31.png   
961  https://i.redd.it/nxsavfoghao31.png   
964  https://i.redd.it/rxwnxbjvw9o31.png   
966  https://i.redd.it/cwlm9ngtz8o31.png   
968  https://i.redd.it/miw0a0lln8o31.jpg   
985      https://i.imgur.com/1d1M6rA.jpg   
986  https://i.redd.it/itcmu1oap5o31.png   
987  https://i.redd.it/q5bd0xh6p5o31.jpg   
988  https://i.redd.it/5l1ev0o4p5o31.jpg   
989  https://i.redd.it/x1l36xm0z4o31.jpg   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

In [83]:
#Number of entries created:
df_fpl['ocr'].notnull().sum()

179

> Some of the output is gibberish - mostly because several of the images are tables/charts and cannot be adequately converted into a comprehensible string.

> It is also interesting to note that the FPL reddit makes far more image posts than the EPL reddit.

#### 8.2.2 Extracting twitter content for link posts <a id='Extract Tweet'></a> 

In [84]:
#Create new columns for tweet content if 'twitter' tag is in media field
df_fpl['tweet_text'] = [extract_tweet(text) if 'https://twitter' in text else np.nan for text in df_fpl['media'].astype(str)]
df_epl['tweet_text'] = [extract_tweet(text) if 'https://twitter' in text else np.nan for text in df_epl['media'].astype(str)]

In [85]:
df_epl[df_epl['tweet_text'].notnull()][['media', 'tweet_text']]

media  \
14                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   {'type': 'twitter.com', 'oembed': {'provider_url': 'https://twitter.com', 'version': '1.0', 'url': 'https://twitter.com/City_Chief/status/1185969839308967937', 'author_name': 'City Chief', 'height': 527, 'width': 350, 'html': '&lt;blockquote class="twitter-video"&gt;&lt;p lang="en" dir="ltr"&gt;📊| Liverpool (17) have failed to equal Manchester City&amp;#39;s record for most consecutive (18) wins in English top flight history.&lt;a href="https://twitter.com/hashtag/olesatthewheel?src=hash&amp;amp;ref_src=twsrc%5Etfw"&gt;#olesatthewheel&lt;/a&gt; &lt;br&gt; &lt;a href="https://t.co/Snq6KhgwcV"&gt;pic.twitter.com/Snq6KhgwcV&lt;/a&gt;&lt;/p&gt;&amp;mdash; City Chief (@City_Chief) &lt;a href="https://twitter.com/City_Chief/status/1185969839308967937?ref_src=twsrc%5Etfw"&gt;October 20, 2019&lt;/a&gt;&lt;/blockquote&gt;\n&lt;script async src="https://platform.twitter.com/widgets.js" charset="utf-8"&gt;&lt;/script&gt;\n', 'author_url': 'https://twitter.com/City_Chief', 'provider_name': 'Twitter', 'cache_age': 3153600000, 'type': 'rich'}}   
76                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [86]:
df_fpl[df_fpl['tweet_text'].notnull()][['media', 'tweet_text']]

media  \
6                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          {'type': 'twitter.com', 'oembed': {'provider_url': 'https://twitter.com', 'version': '1.0', 'url': 'https://twitter.com/BenDinnery/status/1186397405467611136', 'author_name': 'Ben Dinnery', 'height': 433, 'width': 350, 'html': '&lt;blockquote class="twitter-video"&gt;&lt;p lang="en" dir="ltr"&gt;Maddison is still struggling with an ankle problem. &amp;quot;He did really well to put himself out there [vs Burnley]. He’s hardly trained,&amp;quot; said BR. &amp;quot;He could easily have not played, but he wanted to try it. We felt that if he could give us an hour, he’d have done really well.&amp;quot; &lt;a href="https://twitter.com/hashtag/LCFC?src=hash&amp;amp;ref_src=twsrc%5Etfw"&gt;#LCFC&lt;/a&gt; &lt;a href="https://t.co/dpxhxlDuda"&gt;pic.twitter.com/dpxhxlDuda&lt;/a&gt;&lt;/p&gt;&amp;mdash; Ben Dinnery (@BenDinnery) &lt;a href="https://twitter.com/BenDinnery/status/1186397405467611136?ref_src=twsrc%5Etfw"&gt;October 21, 2019&lt;/a&gt;&lt;/blockquote&gt;\n&lt;script async src="https://platform.twitter.com/widgets.js" charset="utf-8"&gt;&lt;/script&gt;\n', 'author_url': 'https://twitter.com/BenDinnery', 'provider_name': 'Twitter', 'cache_age': 3153600000, 'type': 'rich'}}   
13                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                {'type': 'twitter.com', 'oembed': {'provider_url': 'https://twitter.com', 'version': '1.0', 'url': 'https://twitter.com/afcbournemouth/status/1186235758555758593', 'author_name': 'AFC Bournemouth', 'height': 127, 'width': 350, 'html': '&lt;blockquote class="twitter-video"&gt;&lt;p lang="en" dir="ltr"&gt;Congratulations, &lt;a href="https://twitter.com/AaronRamsdale98?ref_src=twsrc%5Etfw"&gt;@AaronRamsdale98&lt;/a&gt; ❤️🖤&lt;/p&gt;&amp;mdash; AFC Bournemouth (@afcbournemouth) &lt;a href="https://twitter.com/afcbournemouth/status/1186235758555758593?ref_src=twsrc%5Etfw"&gt;October 21, 2019&lt;/a&gt;&lt;/blockquote&gt;\n&lt;script async src="https://platform.twitter.com/widgets.js" charset="utf-8"&gt;&lt;/script&gt;\n', 'author_url': 'https://twitter.com/afcbournemouth', 'provider_name': 'Twitter', 'cache_age': 3153600000, 'type': 'rich'}}   
21                                                                                                                                                                                                                                                                                                                                                                                                         

#### 8.2.3 Filling missing values

In [87]:
#fill NA for r/fpl with 'ocr' values
df_fpl['selftext'] = df_fpl['selftext'].fillna(df_fpl['ocr'])

In [88]:
#fill NA for r/fpl with 'tweet_text' values
df_fpl['selftext'] = df_fpl['selftext'].fillna(df_fpl['tweet_text'])

In [89]:
df_fpl['selftext'].isnull().sum()

227

In [90]:
#fill NA for r/fpl with 'ocr' values
df_epl['selftext'] = df_epl['selftext'].fillna(df_epl['ocr'])

In [91]:
#fill NA for r/fpl with 'tweet_text' values
df_epl['selftext'] = df_epl['selftext'].fillna(df_epl['tweet_text'])

In [92]:
df_epl['selftext'].isnull().sum()

434

> Over 400 missing values were filled - the rest of the link posts are links to external websites, which may be problematic to crawl and derive values from. For these, we will just use the post title.

### 8.3 Cleaning, Tokenizing, and Lemmatizing Text  <a id='Cleaning Text'></a> 
<div align="right"><a href='#Table of Contents'>Back to Table of Contents</a></div>

In [93]:
lemmatizer = WordNetLemmatizer() 
#
def clean_text(text):
    #Regex to leave only emojis, text, and numbers
    cleaned_text = re.sub(r":-?[()]|([^A-Za-z\U00010000-\U0010ffff])", 
                          lambda x: " " if x.group(1) else x.group(), text.lower())
    
    
    return cleaned_text

In [94]:
#Clean SELFTEXT
#Run regex to clean text, then tokenize, then lemmatize selftext field
df_fpl['selftext'] = df_fpl['selftext'].astype(str).apply(lambda row: ' '.join([lemmatizer.lemmatize(x) for x in nltk.word_tokenize(clean_text(row))]))
df_epl['selftext'] = df_epl['selftext'].astype(str).apply(lambda row: ' '.join([lemmatizer.lemmatize(x) for x in nltk.word_tokenize(clean_text(row))]))

In [95]:
#Clean COMMENTS
#Run regex to clean text, then tokenize, then lemmatize selftext field
df_fpl['comments'] = df_fpl['comments'].astype(str).apply(lambda row: ' '.join([lemmatizer.lemmatize(x) for x in nltk.word_tokenize(clean_text(row))]))
df_epl['comments'] = df_epl['comments'].astype(str).apply(lambda row: ' '.join([lemmatizer.lemmatize(x) for x in nltk.word_tokenize(clean_text(row))]))

In [96]:
#Clean TITLE
#Run regex to clean text, then tokenize, then lemmatize selftext field
df_fpl['title'] = df_fpl['title'].astype(str).apply(lambda row: ' '.join([lemmatizer.lemmatize(x) for x in nltk.word_tokenize(clean_text(row))]))
df_epl['title'] = df_epl['title'].astype(str).apply(lambda row: ' '.join([lemmatizer.lemmatize(x) for x in nltk.word_tokenize(clean_text(row))]))

In [108]:
df_combined = df_fpl.append(df_epl, ignore_index = True).drop('Unnamed: 0', axis = 1)
df_combined = df_combined.fillna('').replace('nan', '')
#Creates a new column with all text fields combined
df_combined['combined'] = df_combined['title'] + df_combined['selftext'] + df_combined['comments'] 
df_combined

subreddit_name_prefixed                author  \
0                r/FantasyPL              DoTheRax   
1                r/FantasyPL          QuickyGaming   
2                r/FantasyPL              Sad_Weed   
3                r/FantasyPL                FMLFPL   
4                r/FantasyPL               kayeloo   
5                r/FantasyPL                  3amz   
6                r/FantasyPL     strawberrygenius7   
7                r/FantasyPL         fromdowntownn   
8                r/FantasyPL            Ak_Ibrahim   
9                r/FantasyPL         superstoreman   
10               r/FantasyPL         cguinnesstout   
11               r/FantasyPL             FPLFeeker   
12               r/FantasyPL                 mrdiv   
13               r/FantasyPL             FPLFeeker   
14               r/FantasyPL             JLane1996   
15               r/FantasyPL             chapalang   
16               r/FantasyPL           Smudger1928   
17               r/FantasyPL             FPLFeeker   
18               r/FantasyPL         AutoModerator   
19               r/FantasyPL          Mik-Hail-tal   
20               r/FantasyPL        alwayscheating   
21               r/FantasyPL            adishriLFC   
22               r/FantasyPL         AutoModerator   
23               r/FantasyPL      aurorabortrealis   
24               r/FantasyPL         FantasyPL_bot   
25               r/FantasyPL               X17_RDM   
26               r/FantasyPL         TrustMe_I_lie   
27               r/FantasyPL         cguinnesstout   
28               r/FantasyPL         superstoreman   
29               r/FantasyPL       404randomguy404   
...                      ...                   ...   
1957         r/PremierLeague         lcfcfanrobbie   
1958         r/PremierLeague           loyalblue77   
1959         r/PremierLeague    TheReasonableCamel   
1960         r/PremierLeague            Dxpat4real   
1961         r/PremierLeague  SidTheRedditNoob6429   
1962         r/PremierLeague             Wuz314159   
1963         r/PremierLeague          Fisher212121   
1964         r/PremierLeague            dwells2016   
1965         r/PremierLeague    TheReasonableCamel   
1966         r/PremierLeague    TheReasonableCamel   
1967         r/PremierLeague    TheReasonableCamel   
1968         r/PremierLeague    TheReasonableCamel   
1969         r/PremierLeague            Michael-WE   
1970         r/PremierLeague              PandosII   
1971         r/PremierLeague            battshooot   
1972         r/PremierLeague           Funkymonk86   
1973         r/PremierLeague            namankhats   
1974         r/PremierLeague               Kentho9   
1975         r/PremierLeague              DogusEUW   
1976         r/PremierLeague  SidTheRedditNoob6429   
1977         r/PremierLeague                mwukfr   
1978         r/PremierLeague               junok87   
1979         r/PremierLeague       LiveCommentator   
1980         r/PremierLeague             Top1Ranks   
1981         r/PremierLeague             AS05Edits   
1982         r/PremierLeague     BoKnowsYourMother   
1983         r/PremierLeague         tomhunter1904   
1984         r/PremierLeague          JurijFedorov   
1985         r/PremierLeague             Shanewilk   
1986         r/PremierLeague           Therius1994   

                                                                                                                                                                                                                                                                                         title  \
0                                                                                                                                                                                                                                               average of gw is higher than the average of gw   
1                                                                           

In [109]:
df_combined['subreddit_name_prefixed'] = df_combined['subreddit_name_prefixed'].apply(lambda x: 0 if x == 'r/FantasyPL' else 1)
df_combined

subreddit_name_prefixed                author  \
0                           0              DoTheRax   
1                           0          QuickyGaming   
2                           0              Sad_Weed   
3                           0                FMLFPL   
4                           0               kayeloo   
5                           0                  3amz   
6                           0     strawberrygenius7   
7                           0         fromdowntownn   
8                           0            Ak_Ibrahim   
9                           0         superstoreman   
10                          0         cguinnesstout   
11                          0             FPLFeeker   
12                          0                 mrdiv   
13                          0             FPLFeeker   
14                          0             JLane1996   
15                          0             chapalang   
16                          0           Smudger1928   
17                          0             FPLFeeker   
18                          0         AutoModerator   
19                          0          Mik-Hail-tal   
20                          0        alwayscheating   
21                          0            adishriLFC   
22                          0         AutoModerator   
23                          0      aurorabortrealis   
24                          0         FantasyPL_bot   
25                          0               X17_RDM   
26                          0         TrustMe_I_lie   
27                          0         cguinnesstout   
28                          0         superstoreman   
29                          0       404randomguy404   
...                       ...                   ...   
1957                        1         lcfcfanrobbie   
1958                        1           loyalblue77   
1959                        1    TheReasonableCamel   
1960                        1            Dxpat4real   
1961                        1  SidTheRedditNoob6429   
1962                        1             Wuz314159   
1963                        1          Fisher212121   
1964                        1            dwells2016   
1965                        1    TheReasonableCamel   
1966                        1    TheReasonableCamel   
1967                        1    TheReasonableCamel   
1968                        1    TheReasonableCamel   
1969                        1            Michael-WE   
1970                        1              PandosII   
1971                        1            battshooot   
1972                        1           Funkymonk86   
1973                        1            namankhats   
1974                        1               Kentho9   
1975                        1              DogusEUW   
1976                        1  SidTheRedditNoob6429   
1977                        1                mwukfr   
1978                        1               junok87   
1979                        1       LiveCommentator   
1980                        1             Top1Ranks   
1981                        1             AS05Edits   
1982                        1     BoKnowsYourMother   
1983                        1         tomhunter1904   
1984                        1          JurijFedorov   
1985                        1             Shanewilk   
1986                        1           Therius1994   

                                                                                                                                                                                                                                                                                         title  \
0                                                                                                                                                                                                                                               average of gw is higher than the average of gw   
1              

### 8.4 Sentiment Analysis  <a id='Sentiment Analysis'></a> 
<div align="right"><a href='#Table of Contents'>Back to Table of Contents</a></div>

In [121]:
analyser = SentimentIntensityAnalyzer()

In [122]:
df_combined['title_sentiment_neg'] = [analyser.polarity_scores(x)['neg'] for x in df_combined['title']]
df_combined['title_sentiment_neu'] = [analyser.polarity_scores(x)['neu'] for x in df_combined['title']]
df_combined['title_sentiment_pos'] = [analyser.polarity_scores(x)['pos'] for x in df_combined['title']]

In [123]:
df_combined['selftext_sentiment_neg'] = [analyser.polarity_scores(x)['neg'] for x in df_combined['selftext']]
df_combined['selftext_sentiment_neu'] = [analyser.polarity_scores(x)['neu'] for x in df_combined['selftext']]
df_combined['selftext_sentiment_pos'] = [analyser.polarity_scores(x)['pos'] for x in df_combined['selftext']]

In [124]:
df_combined['comments_sentiment_neg'] = [analyser.polarity_scores(x)['neg'] for x in df_combined['comments']]
df_combined['comments_sentiment_neu'] = [analyser.polarity_scores(x)['neu'] for x in df_combined['comments']]
df_combined['comments_sentiment_pos'] = [analyser.polarity_scores(x)['pos'] for x in df_combined['comments']]

In [125]:
df_combined['combined_sentiment_neg'] = [analyser.polarity_scores(x)['neg'] for x in df_combined['combined']]
df_combined['combined_sentiment_neu'] = [analyser.polarity_scores(x)['neu'] for x in df_combined['combined']]
df_combined['combined_sentiment_pos'] = [analyser.polarity_scores(x)['pos'] for x in df_combined['combined']]

### 8.5 Extracting Word Counts

In [131]:
df_combined['title_word_count'] = df_combined['title'].apply(lambda x: int(len(x.split())))
df_combined['selftext_word_count'] = df_combined['selftext'].apply(lambda x: int(len(x.split())))
df_combined['comments_word_count'] = df_combined['comments'].apply(lambda x: int(len(x.split())))
df_combined['combined_word_count'] = df_combined['combined'].apply(lambda x: int(len(x.split())))

### 8.6 Export 

In [132]:
#Fill all NAs before exporting
df_combined = df_combined.fillna('')

In [133]:
df_combined.to_csv(r".\datasets\reddit_cleaned_2.csv")

### Contined in Project3Reddit_EDA